# Experiments of regression on Focal Wealth Dataset
This ipython notebook is an exploration of Focal Wealth Dataset constructed by Adrian. The meaning of columns or classification and procedures to calculate net worth of individuals are according to Michel's knowledge and a "6-factors model". This is a preliminary prototype to see if dataset has enough samples that have comprehensive information for estimating net worth of individuals. 

There are several steps in my experiments.

First, calculate net worth from people with comprehensive information (defined in "6-factors model"). Those data are treated as "ground truth" for training.

Second, use those "ground truth" to train an regression model (the regressors don't need to be restricted within information used to calculate those ground truth samples).

Third, identify those predictors having the most predictive power and then filter the database to generate samples having those information and do the prediction.

Fourth, this process really needs an iterative development and validation, but this would be extremely fun and full of excitement. I can image this would be the first model of such kind in this application. Of course, I need to read some textbooks and papers to find out relevant tools.

In [152]:
import sqlite3
# Build connection with SQLlite
FW_conn = sqlite3.connect('../Database/FocalWealth_20180217.db')

In [153]:
# Initialize a cursor and don't change the database
# https://docs.python.org/2/library/sqlite3.html
FW_cursor = FW_conn.cursor()
# Example (the execute method should be treated as an iterator)
for res in FW_cursor.execute('select count(*) from Company'):
    print res

(77369,)


## Initial glimpse of relevant tables (Company(CapitalIQ), People(CapitalIQ), CompanyShareholders(EMIS), and PeopleToCompanies(CapitalIQ))

In [154]:
print "The sample size of the Company table"
for res in FW_cursor.execute('select count(*) from Company'):
    print res
    
print "The sample size of the People table"
for res in FW_cursor.execute('select count(*) from People'):
    print res
    
print "The sample size of the CompanyShareholders table"
for res in FW_cursor.execute('select count(*) from CompanyShareholders'):
    print res
# ??? Why the CompanyShareholders table have much less rows than the People table?

print "The sample size of the PeopleToCompanies table"
for res in FW_cursor.execute('select count(*) from PeopleToCompanies'):
    print res

The sample size of the Company table
(77369,)
The sample size of the People table
(30330,)
The sample size of the CompanyShareholders table
(8748,)
The sample size of the PeopleToCompanies table
(30330,)


In [155]:
# Find the number of rows not equal to null for CompanyShareholders table
print "The sample size of the CompanyShareholders table with not null PercentageOwned"
for res in FW_cursor.execute('select count(*) from CompanyShareholders where PercentageOwned is not null'):
    print res

The sample size of the CompanyShareholders table with not null PercentageOwned
(4890,)


In [156]:
print "The average percentage owned the CompanyShareholders table with not null PercentageOwned"
for res in FW_cursor.execute('select avg(PercentageOwned) from CompanyShareholders where PercentageOwned is not null'):
    print res

The average percentage owned the CompanyShareholders table with not null PercentageOwned
(40.975881390593116,)


In [157]:
# Read data from the CompanyShareholders table to pandas dataframe
import pandas as pd
df_perc_owned = pd.read_sql_query("""
    select * from CompanyShareholders where PercentageOwned is not null;""", FW_conn)

print "The the first 5 lines of percentage owned in the CompanyShareholders table with not null PercentageOwned"
print(df_perc_owned[:5])

The the first 5 lines of percentage owned in the CompanyShareholders table with not null PercentageOwned
                                        Shareholders  \
0  Manaca S.A. Armazens Gerais e Administracao (9...   
1                      Jose Carlos Librelato (0.10%)   
2                            Aloir Librelato (0.10%)   
3                           Gilmar Librelato (0.10%)   
4              Edp Energias Do Brasil S.A. (100.00%)   

                       Company PercentageOwned  
0  Clarion S.A. Agroindustrial          99.79%  
1               Librelato S.A.           0.10%  
2               Librelato S.A.           0.10%  
3               Librelato S.A.           0.10%  
4                Energest S.A.         100.00%  


In [158]:
import re
df_perc_owned["Shareholders_Name"] = [re.findall('^(.+)[\s]*\({1}',sh)[0].lower() for sh in df_perc_owned["Shareholders"]]
df_perc_owned["PercentageOwned_Num"] = [float(re.findall('(.+)%',sh)[0]) for sh in df_perc_owned["PercentageOwned"]]
df_perc_owned["Company_Lower"] = [name.lower() for name in df_perc_owned["Company"]]
print(df_perc_owned[:5])

                                        Shareholders  \
0  Manaca S.A. Armazens Gerais e Administracao (9...   
1                      Jose Carlos Librelato (0.10%)   
2                            Aloir Librelato (0.10%)   
3                           Gilmar Librelato (0.10%)   
4              Edp Energias Do Brasil S.A. (100.00%)   

                       Company PercentageOwned  \
0  Clarion S.A. Agroindustrial          99.79%   
1               Librelato S.A.           0.10%   
2               Librelato S.A.           0.10%   
3               Librelato S.A.           0.10%   
4                Energest S.A.         100.00%   

                              Shareholders_Name  PercentageOwned_Num  \
0  manaca s.a. armazens gerais e administracao                 99.79   
1                        jose carlos librelato                  0.10   
2                              aloir librelato                  0.10   
3                             gilmar librelato                  0.10   
4 

In [159]:
# Test the regular expression pattern
for idx, sh in enumerate(df_perc_owned["Shareholders"]):
    try:
        re.findall('^(.+)[\s]*\({1}',sh)[0]
    except IndexError as e:
        print idx

In [160]:
import numpy as np
print("Average and standard deviation: %s; %s." % 
      (np.mean(df_perc_owned["PercentageOwned_Num"]),np.std(df_perc_owned["PercentageOwned_Num"])))

Average and standard deviation: 40.9758813906; 36.9717069326.


## Get CompanyName, ExchangeTicker, SecurityTickers, PrimarySector, CompanyType, CompanyStages, EBITDA, TotalRevenue, TotalEnterpriseValue, MarketCapitalization, StockBasedComp, CompensationAndBenefits, TotalCashandSTInvestments, ShortTermInvestments, LongTermInvestments, TotalInvestments from the Company table.

In [161]:
# Read data from the Company table to pandas dataframe
import pandas as pd
df_comp_info = pd.read_sql_query("""
    select CompanyName, ExchangeTicker, SecurityTickers, PrimarySector, CompanyType, CompanyStages, EBITDA, TotalRevenue, 
    TotalEnterpriseValue, MarketCapitalization, StockBasedComp, CompensationAndBenefits, 
    TotalCashandSTInvestments, ShortTermInvestments, LongTermInvestments, TotalInvestments
    from Company 
    where TotalRevenue is not null or
    TotalEnterpriseValue is not null;""", FW_conn)
print "The the first 5 lines of financial information in the Company table with not null TotalRevenue"
print(df_comp_info[:5])

The the first 5 lines of financial information in the Company table with not null TotalRevenue
                             CompanyName ExchangeTicker SecurityTickers  \
0                   Construtora Nm Ltda.           None            None   
1    Construtora Norberto Odebrecht S.A.           None            None   
2                   Construtora OAS S.A.           None            None   
3           Construtora Passarelli Ltda.           None            None   
4  Construtora Paulo Taufik Camasmie S/A           None            None   

            PrimarySector      CompanyType CompanyStages  EBITDA  \
0             Industrials  Private Company          None     NaN   
1             Industrials  Private Company          None -543.40   
2             Industrials  Private Company          None -382.50   
3             Industrials  Private Company          None    2.66   
4  Consumer Discretionary  Private Company          None     NaN   

   TotalRevenue  TotalEnterpriseValue  Market

In [162]:
# Find those non-alphanumeric characters in the company name from EMIS data
EMIS_non_alphanum_set = set([])
for idx, name in enumerate(df_perc_owned["Company"]):
    EMIS_non_alphanum_set = EMIS_non_alphanum_set | set(re.findall('([^a-zA-Z0-9])', name))
print EMIS_non_alphanum_set

set([u' ', u"'", u'&', u')', u'(', u'-', u',', u'/', u'.', u';', u':', u']', u'[', u'?'])


In [163]:
# Find those non-alphanumeric characters in the company name from CapitalIQ data
CIQ_non_alphanum_set = set([])
for idx, name in enumerate(df_comp_info["CompanyName"]):
    CIQ_non_alphanum_set = CIQ_non_alphanum_set | set(re.findall('([^a-zA-Z0-9])', name))
print CIQ_non_alphanum_set

set([u'\xa6', u'\u2013', u'\u2019', u'!', u'\xa0', u'#', u'"', u"'", u'&', u')', u'(', u'+', u'-', u',', u'/', u'.', u':', u'=', u'?', u'>', u'\xc1', u'\xc0', u'\xc3', u'\xc2', u'\xc7', u' ', u'\xc9', u'\xca', u'\xcd', u'\xa3', u'\xd3', u'\xd5', u'\xd4', u'\xdc', u'\xda', u'\\', u'_', u'\xe1', u'\xe0', u'\xe3', u'\xe2', u'\xe4', u'\xe7', u'`', u'\xe9', u'\xeb', u'\xea', u'\xed', u'\xec', u'|', u'\xa9', u'\xf3', u'\xf5', u'\xf4', u'\xf6', u'\xba', u'\xfa', u'\xfc'])


In [164]:
# Find those non-alphanumeric characters in the shareholder name from EMIS data
EMIS_shareholder_non_alphanum_set = set([])
for idx, name in enumerate(df_perc_owned["Shareholders_Name"]):
    EMIS_shareholder_non_alphanum_set = EMIS_shareholder_non_alphanum_set | set(re.findall('([^a-zA-Z0-9])', name))
print EMIS_shareholder_non_alphanum_set

set([u' ', u'-', u'\u2013', u'\xe2', u'\\', u'_', u'\xe1', u'\xe0', u'\xe3', u'"', u'%', u"'", u'\xe7', u'&', u'\xe9', u'(', u'\xea', u'\xed', u'/', u'.', u')', u'\xf3', u':', u'\xf5', u'\xf4', u'\xf6', u';', u'\xfa', u'\xfc'])


In [165]:
for ele in CIQ_non_alphanum_set:
    for idx, name in enumerate(df_comp_info["CompanyName"]):
        if ele in re.findall('([^a-zA-Z0-9])',name):
            print("symbol:%s; index:%s; name:%s" % (ele, idx, name))
            break

symbol:¦; index:2647; name:Fortaleza Distribuiç¦o E Logística Ltda.
symbol:–; index:6051; name:CEMSA – Construções, Engenharia e Montagens S/A
symbol:’; index:3673; name:L’Oréal Brasil Comercial de Cosmeticos Ltda
symbol:!; index:3877; name:Level Up! Interactive S.A.
symbol: ; index:1085; name:Dow Corning do Brasil, Limitada
symbol:#; index:1158; name:Duns_Test (Test Business #02) _ Bir Html_Bid-Opal_Dews_Strings
symbol:"; index:6139; name:Centro de Estudos e Pesquisas "Dr. João Amorim" - Gestão Saúde Embu das Artes
symbol:'; index:570; name:D'Altomare Química Ltda
symbol:&; index:52; name:Contini & Cia. Ltda.
symbol:); index:20; name:Construtora Tenda S.A. (BOVESPA:TEND3)
symbol:(; index:20; name:Construtora Tenda S.A. (BOVESPA:TEND3)
symbol:+; index:2369; name:Ferro + Mineração S.A.
symbol:-; index:24; name:Construtora Varca Scatena Ltda - (RecuperaCAo Judicial)
symbol:,; index:148; name:Cooperativa de Produtores de Cana-de-Açúcar, Açúcar e Álcool do Estado de São Paulo
symbol:/; ind

In [166]:
for ele in EMIS_non_alphanum_set:
    for idx, name in enumerate(df_perc_owned["Company"]):
        if ele in re.findall('([^a-zA-Z0-9])',name):
            print("symbol:%s; index:%s; name:%s" % (ele, idx, name))
            break

symbol: ; index:0; name:Clarion S.A. Agroindustrial
symbol:'; index:1505; name:L'oreal Brasil Comercial De Cosmeticos Ltda
symbol:&; index:21; name:Buschle & Lepper S.A.
symbol:); index:154; name:Tmd Friction Do Brasil S.A. (Indaiatuba)
symbol:(; index:154; name:Tmd Friction Do Brasil S.A. (Indaiatuba)
symbol:-; index:6; name:Cab Cuiaba S/A - Concessionaria de Servicos Publicos de Agua e Esgoto
symbol:,; index:40; name:Prati, Donaduzzi & Cia Ltda.
symbol:/; index:6; name:Cab Cuiaba S/A - Concessionaria de Servicos Publicos de Agua e Esgoto
symbol:.; index:0; name:Clarion S.A. Agroindustrial
symbol:;; index:360; name:Log &amp; Print Dados Variaveis Ltda.
symbol::; index:2723; name:Procergs CIA de Processamentos de Dados do Est Rs Capital:
symbol:]; index:2200; name:J Badim S.A.  [1]
symbol:[; index:2200; name:J Badim S.A.  [1]
symbol:?; index:3069; name:Standard Chartered Bank (Brasil) S.A. ? Banco De Investimento


In [167]:
for ele in EMIS_shareholder_non_alphanum_set:
    for idx, name in enumerate(df_perc_owned["Shareholders_Name"]):
        if ele in re.findall('([^a-zA-Z0-9])',name):
            print("symbol:%s; index:%s; name:%s" % (ele, idx, name))
            break

symbol: ; index:0; name:manaca s.a. armazens gerais e administracao 
symbol:-; index:6; name:companhia de aguas do brasil - cab ambiental 
symbol:–; index:508; name:brazilian private equity fund iii – fip 
symbol:â; index:3631; name: fundo de investimento de ações dinâmica energia 
symbol:\; index:2737; name:digicon s\a 
symbol:_; index:4741; name: outros_pj 
symbol:á; index:47; name:delta agropecuária e participações ltda 
symbol:à; index:3738; name: brc s.à.r.l. 
symbol:ã; index:31; name:ocv administração e participações ltda. 
symbol:"; index:1077; name: government of singapore investment corporation pte ltd "gic" 
symbol:%; index:4684; name: fip saneamento 100% fundo de investimento em participações 
symbol:'; index:55; name:jpmorgan chase bank (banco depositário - adr's) 
symbol:ç; index:26; name:omega desenvolvimento iii fundo de investimento em participações multiestratégia 
symbol:&; index:18; name:fsb vianna & cia ltda. 
symbol:é; index:5; name:nestlé s.a. 
symbol:(; index:55;

In [168]:
for ele in CIQ_non_alphanum_set:
    count = 0
    for idx, name in enumerate(df_comp_info["CompanyName"]):
        if ele in re.findall('([^a-zA-Z0-9])',name):
            count += 1
    print("symbol:%s; count:%s;" % (ele, count))

symbol:¦; count:2;
symbol:–; count:1;
symbol:’; count:1;
symbol:!; count:2;
symbol: ; count:4;
symbol:#; count:6;
symbol:"; count:2;
symbol:'; count:37;
symbol:&; count:284;
symbol:); count:403;
symbol:(; count:404;
symbol:+; count:7;
symbol:-; count:1461;
symbol:,; count:419;
symbol:/; count:2810;
symbol:.; count:10336;
symbol::; count:341;
symbol:=; count:1;
symbol:?; count:5;
symbol:>; count:1;
symbol:Á; count:114;
symbol:À; count:1;
symbol:Ã; count:5;
symbol:Â; count:5;
symbol:Ç; count:4;
symbol: ; count:18219;
symbol:É; count:5;
symbol:Ê; count:2;
symbol:Í; count:8;
symbol:£; count:1;
symbol:Ó; count:20;
symbol:Õ; count:2;
symbol:Ô; count:11;
symbol:Ü; count:2;
symbol:Ú; count:4;
symbol:\; count:1;
symbol:_; count:6;
symbol:á; count:1362;
symbol:à; count:22;
symbol:ã; count:1516;
symbol:â; count:162;
symbol:ä; count:3;
symbol:ç; count:2958;
symbol:`; count:1;
symbol:é; count:1278;
symbol:ë; count:1;
symbol:ê; count:260;
symbol:í; count:750;
symbol:ì; count:1;
symbol:|; count:3;
sy

In [169]:
for ele in EMIS_non_alphanum_set:
    count = 0
    for idx, name in enumerate(df_perc_owned["Company"]):
        if ele in re.findall('([^a-zA-Z0-9])',name):
            count += 1
    print("symbol:%s; count:%s;" % (ele, count))

symbol: ; count:4847;
symbol:'; count:8;
symbol:&; count:41;
symbol:); count:98;
symbol:(; count:98;
symbol:-; count:552;
symbol:,; count:64;
symbol:/; count:353;
symbol:.; count:3582;
symbol:;; count:23;
symbol::; count:4;
symbol:]; count:6;
symbol:[; count:6;
symbol:?; count:1;


In [170]:
for ele in EMIS_shareholder_non_alphanum_set:
    count = 0
    for idx, name in enumerate(df_perc_owned["Shareholders_Name"]):
        if ele in re.findall('([^a-zA-Z0-9])',name):
            count += 1
    print("symbol:%s; count:%s;" % (ele, count))

symbol: ; count:4890;
symbol:-; count:274;
symbol:–; count:5;
symbol:â; count:4;
symbol:\; count:1;
symbol:_; count:1;
symbol:á; count:34;
symbol:à; count:3;
symbol:ã; count:78;
symbol:"; count:3;
symbol:%; count:1;
symbol:'; count:4;
symbol:ç; count:180;
symbol:&; count:28;
symbol:é; count:55;
symbol:(; count:59;
symbol:ê; count:8;
symbol:í; count:17;
symbol:/; count:122;
symbol:.; count:1641;
symbol:); count:58;
symbol:ó; count:13;
symbol::; count:1;
symbol:õ; count:155;
symbol:ô; count:6;
symbol:ö; count:4;
symbol:;; count:6;
symbol:ú; count:16;
symbol:ü; count:1;


In [171]:
# Remove the accented alphabets in the company name in the Company Table (CapitalIQ data)
import unidecode
df_comp_info["CompanyName_Unaccented"] = [unidecode.unidecode(name).lower() for name in df_comp_info["CompanyName"]]
# Remove the accented alphabets in the shareholder name in the CompanyShareholders Table (EMIS data)
df_perc_owned["Shareholders_Name_Unaccented"] = [unidecode.unidecode(name).lower() for name in df_perc_owned["Shareholders_Name"]]
# Transfer the Company Name of EMIS data from unicode to ascii for later string comparison
df_perc_owned["Company_Lower"] = [unidecode.unidecode(name) for name in df_perc_owned["Company_Lower"]] 
# Actually, this doesn't matter because the same string in unicode and ascii are the same

In [172]:
df_perc_owned["Company_Lower"][0]

u'clarion s.a. agroindustrial'

In [173]:
df_comp_info["CompanyName_Unaccented"][0]

'construtora nm ltda.'

In [174]:
df_perc_owned["Shareholders_Name_Unaccented"][0]

'manaca s.a. armazens gerais e administracao '

In [175]:
# Find those non-alphanumeric characters in the company name from CapitalIQ data (after removing accented alphabet)
CIQ_unaccented_non_alphanum_set = set([])
for idx, name in enumerate(df_comp_info["CompanyName_Unaccented"]):
    CIQ_unaccented_non_alphanum_set = CIQ_unaccented_non_alphanum_set | set(re.findall('([^a-zA-Z0-9])', name))
print CIQ_unaccented_non_alphanum_set
# Find those non-alphanumeric characters in the shareholder name from EMIS data (after removing accented alphabet)
EMIS_unaccented_non_alphanum_set = set([])
for idx, name in enumerate(df_perc_owned["Shareholders_Name_Unaccented"]):
    EMIS_unaccented_non_alphanum_set = EMIS_unaccented_non_alphanum_set | set(re.findall('([^a-zA-Z0-9])', name))
print EMIS_unaccented_non_alphanum_set

set([' ', '\\', '_', '!', '`', '#', '"', "'", '&', ')', '(', '+', '-', ',', '/', '.', ':', '=', '|', '?', '>'])
set([' ', '"', '%', "'", '&', ')', '(', '-', '/', '.', ';', ':', '\\', '_'])


In [176]:
# Count the frequency of those non-alphanumeric symbols in CapitalIQ company names
CIQ_unaccented_non_alphanum_dict = {}
num_occu_threshold = int(df_comp_info.shape[0]/1000)
for ele in CIQ_unaccented_non_alphanum_set:
    count = 0
    for idx, name in enumerate(df_comp_info["CompanyName_Unaccented"]):
        if ele in re.findall('(\W)',name):
            count += 1
    if count > num_occu_threshold:
        CIQ_unaccented_non_alphanum_dict[ele] = count
print(CIQ_unaccented_non_alphanum_dict)
# Count the frequency of those non-alphanumeric symbols in EMIS shareholder names
EMIS_unaccented_non_alphanum_dict = {}
num_occu_threshold = int(df_perc_owned.shape[0]/1000)
for ele in EMIS_unaccented_non_alphanum_set:
    count = 0
    for idx, name in enumerate(df_perc_owned["Shareholders_Name_Unaccented"]):
        if ele in re.findall('(\W)',name):
            count += 1
    if count > num_occu_threshold:
        EMIS_unaccented_non_alphanum_dict[ele] = count
print(EMIS_unaccented_non_alphanum_dict)

{' ': 18220, "'": 38, '&': 284, ')': 405, '(': 406, '-': 1462, ',': 419, '/': 2810, '.': 10336, ':': 341}
{' ': 4890, '&': 28, ')': 58, '(': 59, '-': 278, '/': 122, '.': 1641, ';': 6}


In [177]:
EMIS_non_alphanum_dict = {}
num_occu_threshold = int(df_perc_owned.shape[0]/1000)
for ele in EMIS_non_alphanum_set:
    count = 0
    for idx, name in enumerate(df_perc_owned["Company_Lower"]):
        if ele in re.findall('(\W)',name):
            count += 1
    if count > num_occu_threshold:
        EMIS_non_alphanum_dict[ele] = count
print(EMIS_non_alphanum_dict)

{u' ': 4847, u"'": 8, u'&': 41, u')': 98, u'(': 98, u'-': 552, u',': 64, u'/': 353, u'.': 3582, u';': 23, u']': 6, u'[': 6}


In [178]:
# Split company name based on non-alphanumeric sets
# Table from CapitalIQ
patt_non_alphanum = r'[\.\&/:,\'\"\-;\\+=\#`!?>\|\_]' # Note that have to add escape sign before '-', o.w. numbers are ignored
# df_comp_info["CompanyName_Normalized_List"]=""
def Normalize_Name(patt_non_alphanum, target_df, source_col_name, target_col_name, include_parenth):
    """Normalize names by decoding accented alphabet, replacing non-alphabetnumeric characters with
    white space, and spliting based on white space. A tag to mark whether include info in parenthesis."""
    target_df[target_col_name]=""
    for idx,name in enumerate(target_df[source_col_name]):
        comp_name = name
        normalized_list = []
        para_ele = re.findall(r'[\(\[](.+)[\)\]]',comp_name)# Extract inside () or []
        if para_ele:
            comp_name = re.sub(r'\(.+\)', ' ', comp_name)
            if include_parenth:
                para_ele = [y for x in para_ele for y in re.sub(patt_non_alphanum,' ', x).split()]# Flatten a list of lists
                normalized_list.extend(para_ele)
        sa_ele = re.findall(r's[\./]{1}a[\.]?',comp_name)# Extract "s.a." or "s/a", and put "s.a." back in the string.
        if sa_ele:
            for _ in range(len(sa_ele)):
                normalized_list.append('s.a.')
            comp_name = re.sub(r's[\./]{1}a[\.]?', ' ', comp_name)
        ltd_ele = re.findall(r'ltd[a]?[.]?',comp_name)# Extract "ltda." or "ltda" or "ltd"; and put "ltd" back in the string.
        if ltd_ele:
            for _ in range(len(ltd_ele)):
                normalized_list.append('ltd')
            comp_name = re.sub(r'ltd[a]?[.]?', ' ', comp_name)

        comp_name = re.sub(patt_non_alphanum,' ', comp_name)
        normalized_list.extend(comp_name.split())
        print idx, normalized_list, comp_name.split()
        normalized_list.sort()
        target_df.at[idx, target_col_name]= ' '.join(normalized_list)
    
Normalize_Name(patt_non_alphanum,df_comp_info,"CompanyName_Unaccented","CompanyName_Normalized",False)
        

0 ['ltd', 'construtora', 'nm'] ['construtora', 'nm']
1 ['s.a.', 'construtora', 'norberto', 'odebrecht'] ['construtora', 'norberto', 'odebrecht']
2 ['s.a.', 'construtora', 'oas'] ['construtora', 'oas']
3 ['ltd', 'construtora', 'passarelli'] ['construtora', 'passarelli']
4 ['s.a.', 'construtora', 'paulo', 'taufik', 'camasmie'] ['construtora', 'paulo', 'taufik', 'camasmie']
5 ['ltd', 'construtora', 'pelotense'] ['construtora', 'pelotense']
6 ['ltd', 'construtora', 'phoenix'] ['construtora', 'phoenix']
7 ['ltd', 'construtora', 'premold'] ['construtora', 'premold']
8 ['s.a.', 'construtora', 'presidente'] ['construtora', 'presidente']
9 ['s.a.', 'construtora', 'quebec'] ['construtora', 'quebec']
10 ['s.a.', 'construtora', 'queiroz', 'galvao'] ['construtora', 'queiroz', 'galvao']
11 ['ltd', 'construtora', 'remo'] ['construtora', 'remo']
12 ['ltd', 'construtora', 'ribeiro', 'caram'] ['construtora', 'ribeiro', 'caram']
13 ['s.a.', 'construtora', 'sagendra'] ['construtora', 'sagendra']
14 ['s.a.

In [179]:
idx_samp = 559
print df_comp_info["CompanyName_Unaccented"][idx_samp], df_comp_info["CompanyName_Normalized"][idx_samp]

cyrela commercial properties s.a. (bovespa:ccpr3) commercial cyrela properties s.a.


In [180]:
df_comp_info[:20]

CompanyName ExchangeTicker SecurityTickers  \
0                    Construtora Nm Ltda.           None            None   
1     Construtora Norberto Odebrecht S.A.           None            None   
2                    Construtora OAS S.A.           None            None   
3            Construtora Passarelli Ltda.           None            None   
4   Construtora Paulo Taufik Camasmie S/A           None            None   
5             Construtora Pelotense Ltda.           None            None   
6                Construtora Phoenix Ltda           None            None   
7               Construtora Premold Ltda.           None            None   
8             Construtora Presidente S.A.           None            None   
9                  Construtora Quebec S/A           None            None   
10        Construtora Queiroz Galvão S.A.           None            None   
11                  Construtora Remo Ltda           None            None   
12         Construtora Ribeiro Caram Ltda           None            None   
13               Construtora Sagendra S/A           None            None   
14           Construtora Santa Isabel S/A           None            None   
15             Construtora Sepol Ltda Epp           None            None   
16              Construtora Solidum Ltda.           None            None   
17               Construtora Sucesso S/a.           None            None   
18               Construtora Sultepa S.A.           None            None   
19              Construtora Tedesco Ltda.           None            None   

             PrimarySector      CompanyType CompanyStages   EBITDA  \
0              Industrials  Private Company          None      NaN   
1              Industrials  Private Company          None -543.400   
2              Industrials  Private Company          None -382.500   
3              Industrials  Private Company          None    2.660   
4   Consumer Discretionary  Private Company          None      NaN   
5              Industrials  Private Company          None      NaN   
6              Industrials  Private Company          None      NaN   
7              Industrials  Private Company          None      NaN   
8              Real Estate  Private Company          None      NaN   
9              Industrials  Private Company          None      NaN   
10             Industrials  Private Company          None   80.000   
11             Industrials  Private Company          None      NaN   
12  Consumer Discretionary  Private Company          None      NaN   
13             Industrials  Private Company          None      NaN   
14             Industrials  Private Company          None   -1.670   
15             Industrials  Private Company          None      NaN   
16             Industrials  Private Company          None      NaN   
17             Industrials  Private Company          None      NaN   
18             Industrials  Private Company          None    0.562   
19             Industrials  Private Company          None      NaN   

    TotalRevenue  TotalEnterpriseValue  MarketCapitalization  StockBasedComp  \
0          46.40                   NaN                   NaN             NaN   
1         825.80                   NaN                   NaN             NaN   
2        1167.50                   NaN                   NaN             NaN   
3          69.60                   NaN                   NaN             NaN   
4           0.20                   NaN                   NaN             NaN   
5          15.20                   NaN                   NaN             NaN   
6          24.90                   NaN                   NaN             NaN   
7          10.30                   NaN                   NaN             NaN   
8          17.60                   NaN                   NaN             NaN   
9           7.82                   NaN                   NaN             NaN   
10        937.00                   NaN                   NaN             NaN   
11

In [181]:
# Split company name based on non-alphanumeric sets
# Table from EMIS
# df_perc_owned["CompanyName_Normalized_List"]=""

Normalize_Name(patt_non_alphanum,df_perc_owned,"Company_Lower","CompanyName_Normalized",False)

0 ['s.a.', u'clarion', u'agroindustrial'] [u'clarion', u'agroindustrial']
1 ['s.a.', u'librelato'] [u'librelato']
2 ['s.a.', u'librelato'] [u'librelato']
3 ['s.a.', u'librelato'] [u'librelato']
4 ['s.a.', u'energest'] [u'energest']
5 ['ltd', u'nestle', u'brasil'] [u'nestle', u'brasil']
6 ['s.a.', u'cab', u'cuiaba', u'concessionaria', u'de', u'servicos', u'publicos', u'de', u'agua', u'e', u'esgoto'] [u'cab', u'cuiaba', u'concessionaria', u'de', u'servicos', u'publicos', u'de', u'agua', u'e', u'esgoto']
7 ['s.a.', u'copart', u'4', u'participacoes'] [u'copart', u'4', u'participacoes']
8 [u'ssa'] [u'ssa']
9 [u'ssa'] [u'ssa']
10 [u'ssa'] [u'ssa']
11 ['ltd', u'fertilizantes', u'piratini'] [u'fertilizantes', u'piratini']
12 ['ltd', u'tora', u'transp', u'industriais'] [u'tora', u'transp', u'industriais']
13 ['ltd', u'tora', u'transp', u'industriais'] [u'tora', u'transp', u'industriais']
14 ['s.a.', u'csap', u'companhia', u'sul', u'americana', u'de', u'pecuaria'] [u'csap', u'companhia', u'sul',

In [182]:
df_perc_owned[:20]

Shareholders  \
0   Manaca S.A. Armazens Gerais e Administracao (9...   
1                       Jose Carlos Librelato (0.10%)   
2                             Aloir Librelato (0.10%)   
3                            Gilmar Librelato (0.10%)   
4               Edp Energias Do Brasil S.A. (100.00%)   
5                               Nestlé S.A. (100.00%)   
6   Companhia De Aguas Do Brasil - Cab Ambiental (...   
7         Oi S.A. - Em Recuperacao Judicial (100.00%)   
8   Sao Salvador Administracao e Participacoes Ltd...   
9                        Jose Carlos de Souza (1.20%)   
10         Maria Flavia Perilo Vieira e Souza (1.10%)   
11  Fertipar Fertilizantes Do Parana Limitada (100...   
12     Estrela Comercio e Participacoes S.A. (99.00%)   
13              Paulo Sergio Roberto da Silva (1.00%)   
14                              Minerva S.A. (99.99%)   
15     Ot Administracao e Participacoes Ltda (78.70%)   
16                    Dislin Company Limited (20.30%)   
17                  Ruth Gianesella Taurisano (1.00%)   
18                    FSB Vianna & Cia Ltda. (48.30%)   
19         Espolio de Flavio Sa Brito Vianna (37.40%)   

                                              Company PercentageOwned  \
0                         Clarion S.A. Agroindustrial          99.79%   
1                                      Librelato S.A.           0.10%   
2                                      Librelato S.A.           0.10%   
3                                      Librelato S.A.           0.10%   
4                                       Energest S.A.         100.00%   
5                                 Nestle Brasil Ltda.         100.00%   
6   Cab Cuiaba S/A - Concessionaria de Servicos Pu...          80.00%   
7                         Copart 4 Participacoes S.A.         100.00%   
8                                                 SSA          97.70%   
9                                                 SSA           1.20%   
10                                                SSA           1.10%   
11                        Fertilizantes Piratini Ltda         100.00%   
12                       Tora Transp Industriais Ltda          99.00%   
13                       Tora Transp Industriais Ltda           1.00%   
14    Csap - Companhia Sul Americana de Pecuaria S.A.          99.99%   
15             Distribuidora Brasilia De Veiculos S/a          78.70%   
16             Distribuidora Brasilia De Veiculos S/a          20.30%   
17             Distribuidora Brasilia De Veiculos S/a           1.00%   
18                               Simpala Veiculos S/A          48.30%   
19                               Simpala Veiculos S/A          37.40%   

                                   Shareholders_Name  PercentageOwned_Num  \
0       manaca s.a. armazens gerais e administracao                 99.79   
1                             jose carlos librelato                  0.10   
2                                   aloir librelato                  0.10   
3                                  gilmar librelato                  0.10   
4                       edp energias do brasil s.a.                100.00   
5                                       nestlé s.a.                100.00   
6      companhia de aguas do brasil - cab ambiental                 80.00   
7                 oi s.a. - em recuperacao judicial                100.00   
8   sao salvador administracao e participacoes ltda                 97.70   
9                              jose carlos de souza                  1.20   
10               maria flavia perilo vieira e souza                  1.10   
11        fertipar fertilizantes do parana limitada                100.00   
12            estrela comercio e participacoes s.a.                 99.00   
13                    paulo sergio roberto da silva                  1.00   
14                                     minerva s.a.                 99.99   
15            ot administracao e participacoes ltda                 78.70   


In [183]:
# Split shareholders name based on non-alphanumeric sets
# Table from EMIS
# df_perc_owned["Shareholders_Name_Normalized_List"]=""

Normalize_Name(patt_non_alphanum,df_perc_owned,"Shareholders_Name_Unaccented","Shareholders_Name_Normalized",False)

0 ['s.a.', 'manaca', 'armazens', 'gerais', 'e', 'administracao'] ['manaca', 'armazens', 'gerais', 'e', 'administracao']
1 ['jose', 'carlos', 'librelato'] ['jose', 'carlos', 'librelato']
2 ['aloir', 'librelato'] ['aloir', 'librelato']
3 ['gilmar', 'librelato'] ['gilmar', 'librelato']
4 ['s.a.', 'edp', 'energias', 'do', 'brasil'] ['edp', 'energias', 'do', 'brasil']
5 ['s.a.', 'nestle'] ['nestle']
6 ['companhia', 'de', 'aguas', 'do', 'brasil', 'cab', 'ambiental'] ['companhia', 'de', 'aguas', 'do', 'brasil', 'cab', 'ambiental']
7 ['s.a.', 'oi', 'em', 'recuperacao', 'judicial'] ['oi', 'em', 'recuperacao', 'judicial']
8 ['ltd', 'sao', 'salvador', 'administracao', 'e', 'participacoes'] ['sao', 'salvador', 'administracao', 'e', 'participacoes']
9 ['jose', 'carlos', 'de', 'souza'] ['jose', 'carlos', 'de', 'souza']
10 ['maria', 'flavia', 'perilo', 'vieira', 'e', 'souza'] ['maria', 'flavia', 'perilo', 'vieira', 'e', 'souza']
11 ['fertipar', 'fertilizantes', 'do', 'parana', 'limitada'] ['fertipar'

In [184]:
df_perc_owned[:20]

Shareholders  \
0   Manaca S.A. Armazens Gerais e Administracao (9...   
1                       Jose Carlos Librelato (0.10%)   
2                             Aloir Librelato (0.10%)   
3                            Gilmar Librelato (0.10%)   
4               Edp Energias Do Brasil S.A. (100.00%)   
5                               Nestlé S.A. (100.00%)   
6   Companhia De Aguas Do Brasil - Cab Ambiental (...   
7         Oi S.A. - Em Recuperacao Judicial (100.00%)   
8   Sao Salvador Administracao e Participacoes Ltd...   
9                        Jose Carlos de Souza (1.20%)   
10         Maria Flavia Perilo Vieira e Souza (1.10%)   
11  Fertipar Fertilizantes Do Parana Limitada (100...   
12     Estrela Comercio e Participacoes S.A. (99.00%)   
13              Paulo Sergio Roberto da Silva (1.00%)   
14                              Minerva S.A. (99.99%)   
15     Ot Administracao e Participacoes Ltda (78.70%)   
16                    Dislin Company Limited (20.30%)   
17                  Ruth Gianesella Taurisano (1.00%)   
18                    FSB Vianna & Cia Ltda. (48.30%)   
19         Espolio de Flavio Sa Brito Vianna (37.40%)   

                                              Company PercentageOwned  \
0                         Clarion S.A. Agroindustrial          99.79%   
1                                      Librelato S.A.           0.10%   
2                                      Librelato S.A.           0.10%   
3                                      Librelato S.A.           0.10%   
4                                       Energest S.A.         100.00%   
5                                 Nestle Brasil Ltda.         100.00%   
6   Cab Cuiaba S/A - Concessionaria de Servicos Pu...          80.00%   
7                         Copart 4 Participacoes S.A.         100.00%   
8                                                 SSA          97.70%   
9                                                 SSA           1.20%   
10                                                SSA           1.10%   
11                        Fertilizantes Piratini Ltda         100.00%   
12                       Tora Transp Industriais Ltda          99.00%   
13                       Tora Transp Industriais Ltda           1.00%   
14    Csap - Companhia Sul Americana de Pecuaria S.A.          99.99%   
15             Distribuidora Brasilia De Veiculos S/a          78.70%   
16             Distribuidora Brasilia De Veiculos S/a          20.30%   
17             Distribuidora Brasilia De Veiculos S/a           1.00%   
18                               Simpala Veiculos S/A          48.30%   
19                               Simpala Veiculos S/A          37.40%   

                                   Shareholders_Name  PercentageOwned_Num  \
0       manaca s.a. armazens gerais e administracao                 99.79   
1                             jose carlos librelato                  0.10   
2                                   aloir librelato                  0.10   
3                                  gilmar librelato                  0.10   
4                       edp energias do brasil s.a.                100.00   
5                                       nestlé s.a.                100.00   
6      companhia de aguas do brasil - cab ambiental                 80.00   
7                 oi s.a. - em recuperacao judicial                100.00   
8   sao salvador administracao e participacoes ltda                 97.70   
9                              jose carlos de souza                  1.20   
10               maria flavia perilo vieira e souza                  1.10   
11        fertipar fertilizantes do parana limitada                100.00   
12            estrela comercio e participacoes s.a.                 99.00   
13                    paulo sergio roberto da silva                  1.00   
14                                     minerva s.a.                 99.99   
15            ot administracao e participacoes ltda                 78.70   


In [185]:
print df_perc_owned["CompanyName_Normalized"][6], df_perc_owned["Company_Lower"][6]
print df_perc_owned["Shareholders_Name_Normalized"][6], df_perc_owned["Shareholders_Name_Unaccented"][6]

agua cab concessionaria cuiaba de de e esgoto publicos s.a. servicos cab cuiaba s/a - concessionaria de servicos publicos de agua e esgoto
aguas ambiental brasil cab companhia de do companhia de aguas do brasil - cab ambiental 


## Look into what are in paratheses or brackets
What do those elements in brackets mean?

In [186]:
count = 0
for idx, name in enumerate(df_comp_info["CompanyName_Unaccented"]):
    para_ele = re.findall(r'[\(\[](.+)[\)\]]',name)
    if para_ele:
        count += 1
        print idx, para_ele
print count

20 ['bovespa:tend3']
24 ['recuperacao judicial']
33 ['bovespa:ctax3']
281 ['bovespa:corr4']
303 ['bovespa:czlt33']
304 ['bovespa:rlog3']
306 ['bovespa:csan3']
375 ['bovespa:cpfe3']
376 ['bovespa:cpre3']
392 ['bovespa:crde3']
408 ['brasil']
409 ['brasil']
422 ['bovespa:crem3']
435 ['bovespa:crpg5']
486 ['bovespa:hgbs11']
487 ['bovespa:grlv11']
488 ['bovespa:hglg11']
489 ['bovespa:hgre11']
499 ['bovespa:card3']
507 ['bovespa:trpl4']
547 ['bovespa:cvcb3']
558 ['bovespa:cyre3']
559 ['bovespa:ccpr3']
744 ['em recuperacao judicial']
763 ['brazil']
766 ['brasil']
847 ['bovespa:dasa3']
867 ['recuperacao judicial']
894 ['bovespa:pnvl4']
915 ['bovespa:dirr3']
1043 ['bovespa:dohl4']
1052 ['otcpk:dmmo.d']
1081 ['soma:dovl11b']
1140 ['bovespa:dtcy3']
1158 ['test business #02']
1159 ['test business #06']
1160 ['test business #10']
1161 ['test business #13']
1162 ['test business #20']
1163 ['test business #26']
1177 ['bovespa:dtex3']
1195 ['em recuperacao judicial']
1281 ['bovespa:ecor3']
1350 ['bove

In [187]:
count = 0
for idx, name in enumerate(df_perc_owned["Company_Lower"]):
    para_ele = re.findall(r'[\(\[](.+)[\)\]]',name)
    if para_ele:
        count += 1
        print idx, para_ele
print count

154 [u'indaiatuba']
161 [u'sao paulo']
221 [u'closed']
242 [u'recife']
301 [u'brasil']
302 [u'brasil']
303 [u'brasil']
304 [u'brasil']
305 [u'brasil']
390 [u'americana']
391 [u'americana']
563 [u'sinop']
564 [u'sinop']
565 [u'sinop']
567 [u'jundiai']
590 [u'anapolis']
696 [u'varzea paulista) (sao paulo']
758 [u'sao paulo']
759 [u'sao paulo']
760 [u'sao paulo']
761 [u'sao paulo']
787 [u'rio brilhante']
1232 [u'uberlandia']
1233 [u'uberlandia']
1526 [u'salvador']
1606 [u'tp norte']
1690 [u'belo horizonte']
1784 [u'tp sul']
1785 [u'tp sul']
1808 [u'itapage']
2200 [u'1']
2201 [u'1']
2202 [u'1']
2203 [u'1']
2204 [u'1']
2222 [u'belem']
2223 [u'belem']
2224 [u'belem']
2225 [u'belem']
2543 [u'caxias do sul']
2643 [u'closed']
2838 [u'goiania']
2847 [u'brasil']
2900 [u'timbo']
2901 [u'timbo']
2902 [u'timbo']
2903 [u'timbo']
2963 [u'taboao da serra']
3026 [u'barueri']
3027 [u'barueri']
3069 [u'brasil']
3177 [u'1']
3215 [u'uberlandia']
3410 [u'jundiai']
3566 [u'serra']
3567 [u'serra']
3568 [u'serr

In [188]:
count = 0
for idx, name in enumerate(df_perc_owned["Shareholders_Name_Unaccented"]):
    para_ele = re.findall(r'[\(\[](.+)[\)\]]',name)
    if para_ele:
        count += 1
        print idx, para_ele
print count

55 ["banco depositario - adr's"]
255 ['brazil']
505 ['fundos']
653 ['gavea']
784 ['sao paulo']
816 ['brasil']
908 ['olimpia']
1007 ['grupo slc']
1064 ['olimpia']
1104 ['ex reco aster']
1245 ['denmark']
1246 ['denmark']
1515 ['franca']
1518 ['brasil']
1547 ['closed']
1628 ['espolio']
1641 ['"just 4 us"']
1705 ['brasil']
1804 ['denmark']
1816 ['luxemburgo']
1967 ['us']
2429 ['deceased']
2430 ['usa']
2676 ['cariacica']
2840 ['brasil']
2847 ['brasil']
2879 ['brasil']
3025 ['ifc']
3258 ['"brasil capital"']
3676 ['holland']
3690 ['catanduva']
3729 ['sao paulo']
3830 ['conselho e diretoria']
3837 ['ex-nemofeffer s.a.']
3861 ['uk']
3908 ['cba']
3950 ['gestor/administrador - vide item 15.8 a seguir']
3951 ['gestor/administrador - vide item 15.8 a seguir']
3952 ['gestor/administrador - vide item 15.8 a seguir']
3955 ['holdings']
3965 ['garanhuns']
4121 ['brazil']
4135 ['rv']
4196 ['brazil']
4223 ['espanha']
4291 ['familia siaulys']
4292 ['familia depieri']
4293 ['familia baptista']
4306 ['gestor

In [189]:
#Extract all stock exchange names
CIQ_stock_ex_set = set([])
for idx, ticker in enumerate(df_comp_info["ExchangeTicker"]):
    if ticker:
        CIQ_stock_ex_set.add(ticker.split(':')[0])
print CIQ_stock_ex_set

set([u'ASX', u'OTCPK', u'SOMA', u'BOVESPA', u'TSXV', u'NasdaqGM', u'TSX', u'NYSE'])


## Check if a shareholder is a company or not

In [219]:
# Check how many samples are Human based on preliminary standards
comp_name_set = set(df_perc_owned["CompanyName_Normalized"]) | set(df_comp_info["CompanyName_Normalized"])
df_perc_owned["Shareholder_Is_Human"]=""
count = 0
for idx, sh in enumerate(df_perc_owned["Shareholders_Name_Normalized"]):
    if re.findall(r's\.a\.|\bltd\b',sh) or sh in comp_name_set:
        df_perc_owned.at[idx,"Shareholder_Is_Human"] = False
    else:
        df_perc_owned.at[idx,"Shareholder_Is_Human"] = True
        count += 1
print count        

2818


In [222]:
df_perc_owned[df_perc_owned["Shareholder_Is_Human"]==True]

Shareholders  \
1                         Jose Carlos Librelato (0.10%)   
2                               Aloir Librelato (0.10%)   
3                              Gilmar Librelato (0.10%)   
9                          Jose Carlos de Souza (1.20%)   
10           Maria Flavia Perilo Vieira e Souza (1.10%)   
13                Paulo Sergio Roberto da Silva (1.00%)   
16                      Dislin Company Limited (20.30%)   
17                    Ruth Gianesella Taurisano (1.00%)   
19           Espolio de Flavio Sa Brito Vianna (37.40%)   
20                            Tiago Vidal Lohn (30.00%)   
21                   Ludovico Baltaazar Buchle (26.00%)   
22                               Belsa Part. e (25.00%)   
23                        Paulo Hilario Buchle (10.00%)   
24                     Francisco Eberhardt Neto (7.00%)   
25                    Banque Société Générale (100.00%)   
26    Omega Desenvolvimento Iii Fundo de Investiment...   
27     Bjj Income Fundo de Investimento em Participa...   
29     Lambda3 Fundo de Investimento em Participaçõe...   
32                         Osvaldo Carlos Voges (0.10%)   
34     Brasil Pv Fdo. Mutuo Inv. Acoes-c. Livre (25....   
35     Latin America Capital Prtners Ii L. P. Cayman...   
38             Hugo Vinicius Scherer M. da Rosa (0.08%)   
39                       Victor Henrique Foroni (0.08%)   
40                              Luiz Donaduzzi (57.40%)   
41                       Celso Agustinho Prati (28.60%)   
42                              Arno Donaduzzi (14.00%)   
43                   Joao Batista Sergio Murad (99.90%)   
44                               Hugo Loth Neto (0.10%)   
48          CÉlia Peixoto de Barros Lemos Filho (5.87%)   
49                       NÉlia de Souza Peixoto (5.55%)   
...                                                 ...   
4848                   Marcio da Rocha Camargo (23.32%)   
4849                José Janguiê Bezerra Diniz (53.19%)   
4852            Maria Cristina Nunes de Camargo (5.89%)   
4853   Fundo de Investimento de AÇÕes Investimento N...   
4854                             Pedro Bartelle (4.02%)   
4856                      1700480 Ontario Inc. (27.37%)   
4858                Standard Life Aberdeen Plc (15.38%)   
4859                           José Isaac Peres (4.87%)   
4862          Francisco de Queiroz Maia Junior (25.00%)   
4863          Raimundo Alves Cavalcanti Ferraz (25.00%)   
4864                    Adalberto Mota Machado (17.90%)   
4865                 Marcelo Batista de Castro (12.00%)   
4866       Antonio Carlos Ponte de Albuquerque (10.00%)   
4867                Edinardo Ximenes Rodrigues (10.00%)   
4868                           Sussumi Fujioka (45.00%)   
4869                             Teruo Fujioka (45.00%)   
4870                           Katsume Fujioka (10.00%)   
4872                            Treasury Shares (3.65%)   
4874   Fund Petrobras De Seguridade Social Petros (1...   
4875                            Treasury Shares (5.22%)   
4880      Lucia Nabuco De Almeida Braga Rebello (2.25%)   
4881             Luis Antonio Nabuco De A.Braga (2.25%)   
4882     Maria Do Carmo Nabuco De Almeida Braga (2.25%)   
4883             Sylvia Nabuco De Almeida Braga (2.25%)   
4884                        Luciano Snel Correa (1.35%)   
4885                    Cesar Luiz Salazar Saut (1.35%)   
4886                             Luciano Soares (1.15%)   
4887                  Alexandre Petrone Vilardi (1.05%)   
4888                       Guilherme Hinrichsen (0.12%)   
4889                  Marcio De Moraes Palmeira (0.12%)   

                                            Company PercentageOwned  \
1                                    Librelato S.A.           0.10%   
2                                    Librelato S.A.           0.10%   
3                                    Librelato S.A.           0.10%   
9                                               SSA           1.20%   
10                           

In [203]:
df_perc_owned["CompanyName_Normalized"][0]

u'agroindustrial clarion s.a.'

In [204]:
df_perc_owned["Shareholders_Name_Normalized"][0]

'administracao armazens e gerais manaca s.a.'

In [205]:
df_comp_info["CompanyName_Normalized"][0]

'construtora ltd nm'

In [206]:
comp_name_set

{'andrade canellas energia s.a.',
 'catarina de educacional santa sociedade',
 'beverages blue envasadora ltd',
 'gold nx s.a.',
 'comercio e fruta industria mais s.a.',
 'com e industria ltd networker representacao telecom',
 'branco galo s.a. viacao',
 'jamef limitada transportes',
 'das imperador ltd maquinas',
 'ambiental companhia de do estado paulo sao',
 'comercio exterior ltd timbro',
 'a moinho popular s',
 'empreendimentos imobiliarios s.a. verdun',
 'farma farma s.a.',
 u'aereo aviacao e executiva s.a. tam taxi',
 'associados gestores gpa prisionais s.a.',
 'de e geofusion informatica s.a. servicos sistemas',
 'ccps comercio construcap e engenharia s.a.',
 'e imobiliarios legacy negocios participacoes s.a.',
 'abengoa bioenergia brasil s.a.',
 'comercio e industria limitada tintas viwalux',
 'aguas do imperador s.a.',
 '2 caetite energia renovavel s.a.',
 u'comercial ltd maxmix',
 u'compugraf ltd servicos',
 'cruz hospital s.a. santa',
 u'agricola moto s.a. slaviero',
 u'bra

In [223]:
# Check how many samples are Human and the companies he/she own are in the CapitalIQ database
CIQ_comp_name_set = set(df_comp_info["CompanyName_Normalized"])
count = 0
for idx, sh in enumerate(df_perc_owned["Shareholders_Name_Normalized"]):
    if df_perc_owned["Shareholder_Is_Human"][idx] and df_perc_owned["CompanyName_Normalized"][idx] in CIQ_comp_name_set:
        count += 1
print count 

1599


In [213]:
# The following two results show that unicode or ascii code for our case don't matter, because the we only use ascii characters
print df_perc_owned[df_perc_owned["CompanyName_Normalized"]=='lojas renner s.a.']
print df_perc_owned[df_perc_owned["CompanyName_Normalized"]==u'lojas renner s.a.']

                                           Shareholders            Company  \
3950   INC (gestor/administrador - Vide Item 15.8 a ...  Lojas Renner S.A.   
3951   Standard Life Aberdeen Plc (gestor/administra...  Lojas Renner S.A.   
3952   Jpmorgan Asset Management Holdings Inc.(gesto...  Lojas Renner S.A.   

     PercentageOwned                                  Shareholders_Name  \
3950          14.68%   inc (gestor/administrador - vide item 15.8 a ...   
3951          13.88%   standard life aberdeen plc (gestor/administra...   
3952           6.91%   jpmorgan asset management holdings inc.(gesto...   

      PercentageOwned_Num      Company_Lower  \
3950                14.68  lojas renner s.a.   
3951                13.88  lojas renner s.a.   
3952                 6.91  lojas renner s.a.   

                           Shareholders_Name_Unaccented  \
3950   inc (gestor/administrador - vide item 15.8 a ...   
3951   standard life aberdeen plc (gestor/administra...   
3952   jpmorgan 

In [214]:
for idx, sh in enumerate(df_perc_owned["Shareholders_Name_Normalized"]):
    if df_perc_owned["Shareholder_Is_Human"][idx]:
        print("Idx: %s; Name: %s; Normalized Name: %s" % (idx,df_perc_owned["Shareholders_Name"][idx],df_perc_owned["Shareholders_Name_Normalized"][idx]))

Idx: 1; Name: jose carlos librelato ; Normalized Name: carlos jose librelato
Idx: 2; Name:  aloir librelato ; Normalized Name: aloir librelato
Idx: 3; Name:  gilmar librelato ; Normalized Name: gilmar librelato
Idx: 9; Name:  jose carlos de souza ; Normalized Name: carlos de jose souza
Idx: 10; Name:  maria flavia perilo vieira e souza ; Normalized Name: e flavia maria perilo souza vieira
Idx: 13; Name:  paulo sergio roberto da silva ; Normalized Name: da paulo roberto sergio silva
Idx: 16; Name:  dislin company limited ; Normalized Name: company dislin limited
Idx: 17; Name:  ruth gianesella taurisano ; Normalized Name: gianesella ruth taurisano
Idx: 19; Name:  espolio de flavio sa brito vianna ; Normalized Name: brito de espolio flavio sa vianna
Idx: 20; Name: tiago vidal lohn ; Normalized Name: lohn tiago vidal
Idx: 21; Name: ludovico baltaazar buchle ; Normalized Name: baltaazar buchle ludovico
Idx: 22; Name:  belsa part. e ; Normalized Name: belsa e part
Idx: 23; Name:  paulo hila

In [40]:
EMIS_comp_name = list(df_perc_owned["CompanyName_Normalized"])
CIQ_comp_name = list(df_comp_info["CompanyName_Normalized"])
EMIS_comp_name.sort()
CIQ_comp_name.sort()

In [215]:
df_perc_owned_sorted=df_perc_owned.sort_values("CompanyName_Normalized")
df_comp_info_sorted=df_comp_info.sort_values("CompanyName_Normalized")

In [217]:
for idx, row in df_perc_owned_sorted[["CompanyName_Normalized","Company","Shareholder_Is_Human"]].iterrows():
    if row["Shareholder_Is_Human"]:
        print("Index: %s; Company Normalized: %s; Company: %s" % (idx, row["CompanyName_Normalized"], row["Company"]))

Index: 2884; Company Normalized: 10 empreendimento global novo premio prime s.a. spe; Company: Spe 10 Global Premio Novo Prime Empreendimento S.A.
Index: 472; Company Normalized: 4 canal paulo s.a. sao tvsbt; Company: Tvsbt Canal 4 Sao Paulo S.A.
Index: 471; Company Normalized: 4 canal paulo s.a. sao tvsbt; Company: Tvsbt Canal 4 Sao Paulo S.A.
Index: 470; Company Normalized: 4 canal paulo s.a. sao tvsbt; Company: Tvsbt Canal 4 Sao Paulo S.A.
Index: 297; Company Normalized: 7 brasil closed gestao s.a. subsea; Company: Subsea 7 Gestao Brasil S.A. - Closed
Index: 288; Company Normalized: 900 de ltd rapido rodoviarios transportes; Company: Rapido 900 de Transportes Rodoviarios Ltda
Index: 2203; Company Normalized: [1] badim j s.a.; Company: J Badim S.A.  [1]
Index: 2200; Company Normalized: [1] badim j s.a.; Company: J Badim S.A.  [1]
Index: 2204; Company Normalized: [1] badim j s.a.; Company: J Badim S.A.  [1]
Index: 2202; Company Normalized: [1] badim j s.a.; Company: J Badim S.A.  [1]


In [63]:
for idx, row in df_comp_info_sorted[["CompanyName_Normalized","CompanyName"]].iterrows():
    if df_perc_owned_sorted["Shareholder_Is_Human"][idx]:
        print("Index: %s; Company Normalized: %s; Company: %s" % (idx, row["CompanyName_Normalized"], row["CompanyName"]))

Index: 6139; Company Normalized: "dr amorim" artes centro das de e embu estudos gestao joao pesquisas saude; Company: Centro de Estudos e Pesquisas "Dr. João Amorim" - Gestão Saúde Embu das Artes
Index: 6140; Company Normalized: "dr amorim" aruja centro de e estudos joao organizacao pesquisas social; Company: Centro de Estudos e Pesquisas "Dr. João Amorim" - Organização Social Arujá
Index: 1160; Company Normalized: ( 19 b bid bir dews duns html months opal s strings test whith; Company: Duns_Test (Test Business #10) _ Bir Html_Bid-Opal_Dews_Strings.  = > B/S Whith 19 Months (
Index: 3638; Company Normalized: (em comercio de e equipamentos exportacao hospitalares importacao industria ktk ltd rec; Company: Ktk IndUstria, ImportaCAo, ExportaCAo E ComErcio De Equipamentos Hospitalares Ltda (Em Rec
Index: 16083; Company Normalized: 0 2 alegre hoteis ltd pouso; Company: 2.0 Hoteis Pouso Alegre Ltda.
Index: 16077; Company Normalized: 0 2 aracatuba hoteis ltd; Company: 2.0 Hoteis Araçatuba Ltd

In [73]:
df_perc_owned["CompanyName_Normalized"][1500]

u'a assistencia brasil integral medisanitas s.a. saude'

In [74]:
df_comp_info["CompanyName_Normalized"][4755]

'a assistencia brasil integral medisanitas s.a. saude'

In [224]:
keyword_detect_company = ['Company', 'Limited', 'Banque', 'Fundo', 'Partners', 'Prtners', 'Inv', 'Investimento',
                                 'Investimentos', 'Banco', 'Bank', 'Corporate', 'Grupo', 'Prefeitura', 'SARL', 'Municipio',
                                 'Petrobras', 'Associacao', 'Assoc', 'Part', 'capital', 'Treasury','LLC', 'Corporation',
                                 'Parts', 'Companhia', 'Cia', 'Overseas', 'Holding', 'Agric', 'Governo', 'Sec', 'Secretaria',
                                 'Group', 'Estado', 'Investors', 'Asset', 'Empresa', 'Income', 'Brasil', 'Participacoes',
                         'Brasil', 'Recuperacao', 'Judicial', 'credit', 'Desenvolvimento', 'multi', 'Multiestrategia',
                         'Brazilian', 'Logistica', 'Latina', 'America', 'Servico', 'Garantia', 'Tempo', 'Depositario',
                         'Commodities', 'Eletricidade', 'Servs', 'Energia', 'Global', 'Infra', 'Road', 'Economica',
                         'Financiamento', 'Transmissora', 'Eletrica', 'Hospitalares', 'Clinicas', 'Accenture', 'Beneficente',
                         'Shares', 'Services', 'Motorola','Motors','Holdings','Financial', 'Holding', 'Eletricas', 'Federal',
                         'Steel', 'offshores', 'International', 'Mining', 'Resources', 'Economicos', 'Recursos', 'Time', 'world',
                         'video', 'Finance', 'Intl', 'Petroleo', 'Solar', 'Cidade', 'Comercial', 'centrais', 'Seguros', 'fund',
                         'gas','General', 'Mercantille', 'Infraestrutura', 'Mgmt', 'Representacoes', 'Markets', 'Telecom',
                         'co', 'inc', 'Standard', 'Seguranca', 'Solucoes', 'Zurich', 'Pagamento', 'Identificacao', 'Airport',
                         'Industria', 'Material', 'Funcionarios', 'Social', 'Agencia', 'TRANSPORT', 'Nacional', 'Securitaria',
                         'Medicamentos', 'Distribuicao', 'Geografica', 'Produtos', 'Farmaceuticos', 'Civil', 'Auto', 'Tecnologia',
                         'corp', 'Trust', 'Management', 'Assurances', 'Producers', 'Alcool', 'Familia', 'Brazil', 'limitada',
                         'tecidos', 'Educacional', 'Sociedade', 'Positivo', 'life', 'investment', 'gmbh', 'automoveis', 'Usina',
                         'Telecomunicacoes', 'Leasing', 'Settlement', 'Empreendimentos', 'Incorporated', 'Empreed', 'Motores',
                         'Departamento', 'Fundacao', 'Industriais', 'Transportes', 'Engenharia', 'Industrial', 'Tesouraria',
                         'llp', 'Participaciones', 'Fertilizer', 'Sales', 'Funds', 'ind', 'foods', 'Municipalities', 'Lp',
                         'Desenv', 'Consulting', 'Fundos']
len(keyword_detect_company)

176

In [ ]:
bb.append('ff')

In [ ]:
bb

In [ ]:
bb.extend(['uu','vv'])

In [ ]:
bb

In [ ]:
cc = "aaaa3fdfe a332"

In [ ]:
cc.split()